In [1]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from keras.callbacks import ModelCheckpoint


In [2]:
merged = pd.read_csv(r'C:\Users\jerin\Downloads\lbnlbldg59\lbnlbldg59\lbnlbldg59.processed\LBNLBLDG59\clean_Bldg59_2018to2020\clean data\long_merge.csv')

zone = "47"

if zone in ["36", "37", "38", "39", "40", "41", "42", "64", "65", "66", "67", "68", "69", "70"]:
    rtu = "rtu_001"
    wing = "hvac_N"
elif zone in ["18", "25", "26", "45", "48", "55", "56", "61"]:
    rtu = "rtu_003"
    wing = "hvac_S"
elif zone in ["16", "17", "21", "22", "23", "24", "46", "47", "51", "52", "53", "54"]:
    rtu = "rtu_004"
    wing = "hvac_S"
else:
    rtu = "rtu_002"
    wing = "hvac_N"
#merged is the dataframe
sorted = merged[["date"]+[col for col in merged.columns if zone in col or rtu in col or wing in col]+["hp_hws_temp", "aru_001_cwr_temp" , "aru_001_cws_fr_gpm" ,"aru_001_cws_temp","aru_001_hwr_temp" ,"aru_001_hws_fr_gpm" ,"aru_001_hws_temp"]]
sorted

date  zone_047_hw_valve  rtu_004_sat_sp_tn  \
0        2018-01-01 00:00:00              100.0               69.0   
1        2018-01-01 00:01:00              100.0               69.0   
2        2018-01-01 00:02:00              100.0               69.0   
3        2018-01-01 00:03:00              100.0               69.0   
4        2018-01-01 00:04:00              100.0               69.0   
...                      ...                ...                ...   
2072149  2020-12-31 23:58:00              100.0               68.0   
2072150  2020-12-31 23:58:00              100.0               68.0   
2072151  2020-12-31 23:59:00              100.0               68.0   
2072152  2020-12-31 23:59:00              100.0               68.0   
2072153  2021-01-01 00:00:00              100.0               68.0   

         zone_047_temp  zone_047_fan_spd  rtu_004_fltrd_sa_flow_tn  \
0                 67.5              20.0                  9265.604   
1                 67.5              20.0                  9265.604   
2                 67.5              20.0                  9708.240   
3                 67.5              20.0                  9611.638   
4                 67.5              20.0                  9215.110   
...                ...               ...                       ...   
2072149           63.2              20.0                 18884.834   
2072150           63.2              20.0                 18884.834   
2072151           63.2              20.0                 19345.508   
2072152           63.2              20.0                 19345.508   
2072153           63.2              20.0                 18650.232   

         rtu_004_sa_temp  rtu_004_pa_static_stpt_tn  rtu_004_oa_flow_tn  \
0                   66.1                       0.06            0.000000   
1                   66.0                       0.06         6572.099162   
2                   66.1                       0.06         7628.832542   
3                   66.1                       0.06         7710.294617   
4                   66.0                       0.06         7139.184090   
...                  ...                        ...                 ...   
2072149             64.4                       0.06         2938.320000   
2072150             64.4                       0.06         2938.320000   
2072151             64.3                       0.06         3154.390000   
2072152             64.3                       0.06         3154.390000   
2072153             64.1                       0.06         3076.270000   

         rtu_004_oadmpr_pct  ...  zone_047_heating_sp  Unnamed: 47_y  \
0                      28.0  ...                  NaN            NaN   
1                      28.0  ...                  NaN            NaN   
2                      28.0  ...                  NaN            NaN   
3                      28.0  ...                  NaN            NaN   
4                      28.0  ...                  NaN            NaN   
...                     ...  ...                  ...            ...   
2072149                23.4  ...                 71.0           69.0   
2072150                23.4  ...                 71.0           69.0   
2072151                23.4  ...                 71.0           69.0   
2072152                23.4  ...                 71.0           69.0   
2072153                22.9  ...                 71.0           69.0   

            hvac_S  hp_hws_temp  aru_001_cwr_temp  aru_001_cws_fr_gpm  \
0              NaN         75.3               NaN                 NaN   
1              NaN         75.3               NaN                 NaN   
2              NaN         75.3               NaN                 NaN   
3              NaN         75.3               NaN                 NaN   
4              NaN         75.3               NaN                 NaN   
...            ...          ...               ...                 ...   
2072149  23.145000        123.8             56.25               5

In [3]:
final_df = sorted.copy()
final_df['date'] = pd.to_datetime(final_df['date'], format = "%Y-%m-%d %H:%M:%S")
final_df = final_df[ (final_df.date.dt.date >date(2019, 4, 1)) & (final_df.date.dt.date< date(2020, 2, 15))]
final_df.isna().sum()

date                                          0
zone_047_hw_valve                             0
rtu_004_sat_sp_tn                             0
zone_047_temp                                 0
zone_047_fan_spd                              0
rtu_004_fltrd_sa_flow_tn                      0
rtu_004_sa_temp                               0
rtu_004_pa_static_stpt_tn                     0
rtu_004_oa_flow_tn                            0
rtu_004_oadmpr_pct                            0
rtu_004_econ_stpt_tn                          0
rtu_004_ra_temp                               0
rtu_004_oa_temp                               0
rtu_004_ma_temp                               0
rtu_004_sf_vfd_spd_fbk_tn                     0
rtu_004_rf_vfd_spd_fbk_tn                     0
rtu_004_fltrd_gnd_lvl_plenum_press_tn         0
rtu_004_fltrd_lvl2_plenum_press_tn            0
zone_047_cooling_sp                           0
Unnamed: 47_x                            394570
zone_047_heating_sp                     

In [4]:
testdataset_df = final_df[(final_df.date.dt.date <date(2019, 11, 8))]

traindataset_df = final_df[ (final_df.date.dt.date >date(2019, 11, 8))]

testdataset = testdataset_df[['rtu_004_oa_temp','rtu_004_ra_temp','hp_hws_temp','rtu_004_oa_flow_tn','rtu_004_oadmpr_pct',
                    'rtu_004_sat_sp_tn','rtu_004_rf_vfd_spd_fbk_tn','rtu_004_ma_temp','rtu_004_sa_temp','rtu_004_fltrd_sa_flow_tn',
                    'rtu_004_sf_vfd_spd_fbk_tn']].values


traindataset = traindataset_df[['rtu_004_oa_temp','rtu_004_ra_temp','hp_hws_temp','rtu_004_oa_flow_tn','rtu_004_oadmpr_pct',
                    'rtu_004_sat_sp_tn','rtu_004_rf_vfd_spd_fbk_tn','rtu_004_ma_temp','rtu_004_sa_temp','rtu_004_fltrd_sa_flow_tn',
                    'rtu_004_sf_vfd_spd_fbk_tn']].values

In [5]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')


scaler = MinMaxScaler(feature_range=(0, 1))
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [47]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x1,x2,x3,x4,x5,x6,x7,x8,x9,Y = [],[],[],[],[],[],[],[],[],[]
    for i in range(len(dataset)-time_step-1):
        x1.append(dataset[i:(i+time_step), 0])
        x2.append(dataset[i:(i+time_step), 1])
        x3.append(dataset[i:(i+time_step), 2])
        x4.append(dataset[i:(i+time_step), 3])
        x5.append(dataset[i:(i+time_step), 4])
        x6.append(dataset[i:(i+time_step), 5])
        x7.append(dataset[i:(i+time_step), 6])
        x8.append(dataset[i:(i+time_step), 7])
        # x9.append(dataset[i:(i+time_step), 8])
        Y.append([dataset[i + time_step, 7]])
    x1,x2,x3,x4,x5,x6,x7,x8 =  np.array(x1),np.array(x2),np.array(x3), np.array(x4),np.array(x5),np.array(x6),np.array(x7),np.array(x8)#,np.array(x9)
    Y = np.reshape(Y,(len(Y),1))
    return np.stack([x1,x2,x3,x4,x5,x6,x7,x8],axis=2),Y




time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=1))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm2.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10, batch_size=64, verbose=1, callbacks=[checkpoint_callback])


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/10
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0071
Epoch 1: val_loss improved from inf to 0.01145, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 77s 23ms/step - loss: 0.0071 - val_loss: 0.0115
Epoch 2/10
3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0013
Epoch 2: val_loss improved from 0.01145 to 0.01144, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 73s 23ms/step - loss: 0.0013 - val_loss: 0.0114
Epoch 3/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 0.0010
Epoch 3: val_loss improved from 0.01144 to 0.00729, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 71s 22ms/step - loss: 0.0010 - val_loss: 0.0073
Epoch 4/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 5.5876e-04
Epoch 4: val_loss improved from 0.00729 to 0.00409, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 73s 23ms/step - loss: 5.5871e-04 - val_loss: 0.0041
Epoch 5/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 14ms/step - loss: 3.9261e-04
Epoch 

In [45]:
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - loss: 1.8977e-04
Epoch 1: val_loss improved from inf to 0.01131, saving model to lstm2.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 94s 29ms/step - loss: 1.8977e-04 - val_loss: 0.0113
Epoch 2/5
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.7357e-04
Epoch 2: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 91s 28ms/step - loss: 1.7358e-04 - val_loss: 0.0123
Epoch 3/5
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.6701e-04
Epoch 3: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 92s 28ms/step - loss: 1.6701e-04 - val_loss: 0.0127
Epoch 4/5
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step - loss: 1.7043e-04
Epoch 4: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 91s 28ms/step - loss: 1.7043e-04 - val_loss: 0.0131
Epoch 5/5
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - loss: 1.6319e-04
Epoch 5: val_loss did not improve from 0.01131
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 104s 32m

In [48]:
# train_predict = model.predict(X_train)
test_predict = model.predict(X_test)

9900/9900 ━━━━━━━━━━━━━━━━━━━━ 34s 3ms/step


In [49]:
%matplotlib qt
#'rtu_004_ma_temp','rtu_004_sa_temp'
var = 0
plt.plot(testdataset_df['date'][31:],y_test, label='Original Testing Data', color='blue')
plt.plot(testdataset_df['date'][31:],test_predict, label='Predicted Testing Data', color='red',alpha=0.8)
# anomalies = np.where(abs(test_predict[:,var] - y_test[:,var]) > 0.38)[0]
# plt.scatter(anomalies,test_predict[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [50]:
from tensorflow.keras.models import load_model
# model.save("MA_temp_model.h5") 
# loaded_model = load_model("MA_temp_model.h5")

ENERGY DATA

In [3]:
zone =  ["18", "25", "26", "45", "48", "55", "56", "61","16", "17", "21", "23", "24", "46", "47", "51", "52", "53", "54"]
rtu = ["rtu_001","rtu_002","rtu_003","rtu_004"]
wing = ["hvac_N","hvac_S"]
# any(sub in col for sub in zone) or
energy_data = merged[["date"]+[col for col in merged.columns if any(sub in col for sub in wing) or any(sub in col for sub in rtu)]]
df_filtered = energy_data[[col for col in energy_data.columns if 'Unnamed' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'co2' not in col]]
df_filtered = df_filtered[[col for col in df_filtered.columns if 'templogger' not in col]]
# df_filtered = df_filtered.dropna()
df_filtered.head(2)

date  rtu_001_sat_sp_tn  rtu_002_sat_sp_tn  \
0  2018-01-01 00:00:00               68.0               70.0   
1  2018-01-01 00:01:00               68.0               70.0   

   rtu_003_sat_sp_tn  rtu_004_sat_sp_tn  rtu_001_fltrd_sa_flow_tn  \
0               65.0               69.0                 14131.449   
1               65.0               69.0                 14164.429   

   rtu_002_fltrd_sa_flow_tn  rtu_003_fltrd_sa_flow_tn  \
0                 13998.757                 13558.539   
1                 14065.259                 13592.909   

   rtu_004_fltrd_sa_flow_tn  rtu_001_sa_temp  ...  \
0                  9265.604             67.6  ...   
1                  9265.604             67.6  ...   

   rtu_001_fltrd_gnd_lvl_plenum_press_tn  \
0                                  0.030   
1                                  0.031   

   rtu_002_fltrd_gnd_lvl_plenum_press_tn  \
0                                   0.04   
1                                   0.04   

   rtu_003_fltrd_gnd_lvl_plenum_press_tn  \
0                                   0.04   
1                                   0.04   

   rtu_004_fltrd_gnd_lvl_plenum_press_tn  rtu_001_fltrd_lvl2_plenum_press_tn  \
0                                  0.047                               0.050   
1                                  0.043                               0.048   

   rtu_002_fltrd_lvl2_plenum_press_tn  rtu_003_fltrd_lvl2_plenum_press_tn  \
0                                0.05                                0.05   
1                                0.05                                0.04   

   rtu_004_fltrd_lvl2_plenum_press_tn  hvac_N  hvac_S  
0                               0.050     NaN     NaN  
1                               0.046     NaN     NaN  

[2 rows x 59 columns]

In [4]:
df_filtered['date'] = pd.to_datetime(df_filtered['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = df_filtered[ (df_filtered.date.dt.date >date(2019, 4, 1)) & (df_filtered.date.dt.date< date(2020, 2, 15))]
# df_filtered.isna().sum()
if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

There are NA values in the DataFrame columns.


In [5]:
testdataset_df = df_filtered[(df_filtered.date.dt.date <date(2019, 8, 21))]

traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

testdataset = testdataset_df.drop(columns=["date"]).values

traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [6]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = MinMaxScaler(feature_range=(0, 1))
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [7]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = [[] for _ in range(58)] 
    Y = []
    for i in range(len(dataset) - time_step - 1):
        for j in range(58):
            x[j].append(dataset[i:(i + time_step), j])
        Y.append([dataset[i + time_step, 56],dataset[i + time_step, 57]])
    x= [np.array(feature_list) for feature_list in x]
    Y = np.reshape(Y,(len(Y),2))
    return np.stack(x,axis=2),Y

time_step = 60
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)


model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=50))
model.add(Dense(units=2))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm3.keras"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=15, batch_size=64, verbose=1, callbacks=[checkpoint_callback])


c:\Users\jerin\anaconda3\envs\smartbuilding\Lib\site-packages\keras\src\layers\rnn\rnn.py:205: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/15
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step - loss: 0.0038
Epoch 1: val_loss improved from inf to 0.00894, saving model to lstm3.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 144s 44ms/step - loss: 0.0038 - val_loss: 0.0089
Epoch 2/15
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step - loss: 5.4854e-04
Epoch 2: val_loss improved from 0.00894 to 0.00529, saving model to lstm3.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 137s 43ms/step - loss: 5.4854e-04 - val_loss: 0.0053
Epoch 3/15
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step - loss: 5.0405e-04
Epoch 3: val_loss did not improve from 0.00529
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 129s 40ms/step - loss: 5.0405e-04 - val_loss: 0.0063
Epoch 4/15
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step - loss: 4.9573e-04
Epoch 4: val_loss did not improve from 0.00529
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 131s 41ms/step - loss: 4.9572e-04 - val_loss: 0.0061
Epoch 5/15
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step - loss: 4.9666e-04
Epoch 5: val_loss did not improve from 0.00529
3220/

In [39]:
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=10, batch_size=64, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/10
3218/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0050
Epoch 1: val_loss improved from inf to 0.03991, saving model to lstm3.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 68s 21ms/step - loss: 0.0050 - val_loss: 0.0399
Epoch 2/10
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0050
Epoch 2: val_loss did not improve from 0.03991
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 67s 21ms/step - loss: 0.0050 - val_loss: 0.0480
Epoch 3/10
3219/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0048
Epoch 3: val_loss did not improve from 0.03991
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 67s 21ms/step - loss: 0.0048 - val_loss: 0.0474
Epoch 4/10
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0047
Epoch 4: val_loss did not improve from 0.03991
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 68s 21ms/step - loss: 0.0047 - val_loss: 0.0492
Epoch 5/10
3217/3220 ━━━━━━━━━━━━━━━━━━━━ 0s 15ms/step - loss: 0.0048
Epoch 5: val_loss improved from 0.03991 to 0.03753, saving model to lstm3.keras
3220/3220 ━━━━━━━━━━━━━━━━━━━━ 68s 21

In [8]:
test_predict1 = model.predict(X_test)
# train_predict1 = model.predict(X_train)

6344/6344 ━━━━━━━━━━━━━━━━━━━━ 47s 7ms/step


In [10]:
%matplotlib qt
var = 0
plt.plot(testdataset_df['date'][61:],y_test[:,0], label='Original Testing Data', color='blue')
plt.plot(testdataset_df['date'][61:],test_predict1[:,0], label='Predicted Testing Data', color='red',alpha=0.8)
# anomalies = np.where(abs(test_predict[:,var] - y_test[:,var]) > 0.38)[0]
# plt.scatter(anomalies,test_predict[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [11]:
from tensorflow.keras.models import load_model
model.save("energy_model.h5") 

In [8]:
%matplotlib qt
plt.plot(df_filtered['date'],df_filtered['hvac_S'])
plt.plot(df_filtered['date'],df_filtered['rtu_003_sf_vfd_spd_fbk_tn'])
plt.plot(df_filtered['date'],df_filtered['zone_025_temp'])